In [143]:
import geopandas as gpd
import pandas as pd
import osmnx as ox
import folium
from shapely.geometry import shape


cycle_graph = ox.load_graphml("../data/valencia_cycling_network.graphml")

## Public water fountains

Data loading

In [144]:
fuentes_publicas = pd.read_csv("../data/fonts_publiques.csv")

Viewing what geo_shap contains

In [145]:
val = fuentes_publicas["geo_shape"].iloc[0]
print(val, type(val))


{'type': 'Feature', 'geometry': {'coordinates': [-0.3245649933146064, 39.470317839583906], 'type': 'Point'}, 'properties': {}} <class 'str'>


Parse the string column to a dict, then to Shapely geometry

In [146]:
import ast

# parsear la columna de strings a dict, luego a geometría Shapely
fuentes_publicas["geometry"] = fuentes_publicas["geo_shape"].apply(
    lambda s: shape(ast.literal_eval(s))
)


Transforming dataframe to gpd

In [147]:
def get_valenbisi_stations(valenbisi_data):
    """
    Extract Valenbisi stations from the Valenbisi data.

    Parameters:
        valenbisi_data (DataFrame): A DataFrame containing Valenbisi data.

    Returns:
        GeoDataFrame: A GeoDataFrame containing the Valenbisi stations.
    """

    # Convert the DataFrame to a GeoDataFrame
    gdf = gpd.GeoDataFrame(valenbisi_data, geometry=valenbisi_data["geometry"])
    gdf.set_crs(epsg=4326, inplace=True)  # Set the coordinate reference system

    return gdf

In [148]:
fuentes_publicas_gpd = get_valenbisi_stations(fuentes_publicas)

Showing the transformation

In [149]:
fuentes_publicas_gpd

objectid                                  calle codigo  \
0           5  PASEO MARITIMO/HISTORIADOR COLOMA--2ª   1151   
1           9   BULEVAR SUR - BARRACA AUSIAS MARCH 1   1040   
2          11                      PLAZA DEL MERCADO    110   
3          17               JARDIN PLAZA DE LA REINA    104   
4          22            CEMENTERIO GENERAL SEC 20-1   C121   
..        ...                                    ...    ...   
827       230          PLATERO SUAREZ /CALLE SAGUNTO    509   
828       267                AVDA. BLASCO IBAÑEZ, 96   1312   
829       276          PLAZA JOAQUIN MUÑOZ PEIRATS 1   1607   
830       150           PL DOCTOR LORENZO DE LA FLOR   1155   
831       159          CEMENTERIO GENERAL SEC 6 IZDA   C113   

                                                  foto  \
0    http://mapas.valencia.es/WebsMunicipales/layar...   
1    http://mapas.valencia.es/WebsMunicipales/layar...   
2    http://mapas.valencia.es/WebsMunicipales/layar...   
3    http://mapas.valencia.es/WebsMunicipales/layar...   
4    http://mapas.valencia.es/WebsMunicipales/layar...   
..                                                 ...   
827  http://mapas.valencia.es/WebsMunicipales/layar...   
828  http://mapas.valencia.es/WebsMunicipales/layar...   
829  http://mapas.valencia.es/WebsMunicipales/layar...   
830  http://mapas.valencia.es/WebsMunicipales/layar...   
831  http://mapas.valencia.es/WebsMunicipales/layar...   

                                             geo_shape  \
0    {'type': 'Feature', 'geometry': {'coordinates'...   
1    {'type': 'Feature', 'geometry': {'coordinates'...   
2    {'type': 'Feature', 'geometry': {'coordinates'...   
3    {'type': 'Feature', 'geometry': {'coordinates'...   
4    {'type': 'Feature', 'geometry': {'coordinates'...   
..                                                 ...   
827  {'type': 'Feature', 'geometry': {'coordinates'...   
828  {'type': 'Feature', 'geometry': {'coordinates'...   
829  {'type': 'Feature', 'geometry': {'coordinates'...   
830  {'type': 'Feature', 'geometry': {'coordinates'...   
831  {'type': 'Feature', 'geometry': {'coordinates'...   

                                          geo_point_2d  \
0    {'lon': -0.3245649933146064, 'lat': 39.4703178...   
1    {'lon': -0.37167000776736375, 'lat': 39.445251...   
2    {'lon': -0.37922498535436144, 'lat': 39.474571...   
3    {'lon': -0.37553501058701816, 'lat': 39.474624...   
4    {'lon': -0.3986200087544989, 'lat': 39.4429817...   
..                                                 ...   
827  {'lon': -0.37407299938987454, 'lat': 39.485198...   
828  {'lon': -0.35000500025418557, 'lat': 39.474304...   
829  {'lon': -0.3951179978157639, 'lat': 39.4869956...   
830  {'lon': -0.33100999912996454, 'lat': 39.469399...   
831  {'lon': -0.3980959950145709, 'lat': 39.4459724...   

                      geometry  
0    POINT (-0.32456 39.47032)  
1    POINT (-0.37167 39.44525)  
2    POINT (-0.37922 39.47457)  
3    POINT (-0.37554 39.47462)  
4    POINT (-0.39862 39.44298)  
..                         ...  
827   POINT (-0.37407 39.4852)  
828   POINT (-0.35001 39.4743)  
829    POINT (-0.39512 39.487)  
830   POINT (-0.33101 39.4694)  
831   POINT (-0.3981 39.44597)  

[832 rows x 7 columns]

Creating the map with sources

In [150]:
def create_map_with_fonts(graph, stations_gdf, title):
    """
    Create a folium map with the cycling network and Valenbisi stations.

    Parameters:
        graph: The cycling network graph.
        stations_gdf (GeoDataFrame): A GeoDataFrame containing Valenbisi stations.
        title (str): The title of the map.

    Returns:
        folium.Map: A folium map object.
    """
    m = folium.Map(
        location=[39.4699, -0.3763],  # Centered on Valencia
        zoom_start=13,
        tiles="OpenStreetMap",
    )
    # for _, row in stations_gdf.iterrows():
    #     folium.Marker(
    #         location=[row.geometry.y, row.geometry.x],
    #         popup=row["address"],
    #         icon=folium.Icon(color="red"),
    #     ).add_to(m)

    # Add the cycling network edges to the map
    for t in graph.edges(data=True):
        ini, fin, info = t
        start = (graph.nodes[ini]["y"], graph.nodes[ini]["x"])
        end = (graph.nodes[fin]["y"], graph.nodes[fin]["x"])
        folium.PolyLine(
            locations=[start, end], color="blue", weight=2, opacity=0.8
        ).add_to(m)
    for _, row in stations_gdf.iterrows():
        folium.Marker(
            location=[row.geometry.y, row.geometry.x],
            popup=row["calle"],
            icon=folium.Icon(color="blue", icon="tint", prefix="fa"),
        ).add_to(m)
    m.get_root().html.add_child(folium.Element(f"<h3>{title}</h3>"))
    return m


# Create maps with Valenbisi stations
# walk_map = create_map_with_stations(
#     walk_graph, geovalenbisi_walk, "Walking Network with Valenbisi Stations"
# )

cycle_map = create_map_with_fonts(
    cycle_graph, fuentes_publicas_gpd, "Cycling Network with Valenbisi Stations"
)

cycle_map

### Está mal

In [151]:
# import osmnx as ox
# import numpy as np


# def get_nearest_water_fountains_on_route(
#     graph, distancia, route_nodes, type_displacement, temperatura
# ):
#     """
#     Find the nearest public water fountains along a given route.

#     Parameters:
#         graph: The cycling network graph.
#         route_nodes (list): A list of nodes representing the route.
#         max_distance (float): The maximum distance from the route to consider a fountain.

#     Returns:
#         list: A list of dictionaries containing the fountain node and its distance from the route.
#     """
#     fountains = []

#     start_node = route_nodes[0]
#     end_node = route_nodes[-1]
#     # Get the coordinates of the start and end nodes
#     start_coords = (graph.nodes[start_node]["y"], graph.nodes[start_node]["x"])
#     end_coords = (graph.nodes[end_node]["y"], graph.nodes[end_node]["x"])
#     frecuencia_paradas_por_temperatura = {
#         "frio": {
#             "min_temp": -50,  # Valor mínimo (inferior a 10°C)
#             "max_temp": 10,
#             "Caminando": 7,  # minutos parar caminar
#             "En Bicicleta": 12,  # minutos parar bicileta
#         },
#         "ideal": {
#             "min_temp": 15,
#             "max_temp": 25,
#             "Caminando": 5,  # minutos parar caminar
#             "En Bicicleta": 9,  # minutos parar bicileta
#         },
#         "calor_extremo": {
#             "min_temp": 30,
#             "max_temp": 50,  # Valor máximo (superior a 30°C)
#             "Caminando": 3,  # minutos parar caminar
#             "En Bicicleta": 6,  # minutos parar bicileta
#         },
#     }

#     def obtener_frecuencia_paradas():
#         if temperatura < 10:
#             return frecuencia_paradas_por_temperatura["frio"][type_displacement]
#         elif 15 <= temperatura <= 25:
#             return frecuencia_paradas_por_temperatura["ideal"][type_displacement]
#         elif temperatura > 30:
#             return frecuencia_paradas_por_temperatura["calor_extremo"][
#                 type_displacement
#             ]
#         else:
#             return False

#     # Ejemplo de uso:

#     # Calculate the midpoint of the segment
#     mid_coords = (
#         (start_coords[0] + end_coords[0]) / 2,
#         (start_coords[1] + end_coords[1]) / 2,
#     )

#     if type_displacement == "Caminando":
#         max_distance = 150
#         velocidad_cam = 1  # m/s al haber semaforos, normalmente se camina a 1.4 m/s
#         frecuencia_paradas = obtener_frecuencia_paradas()

#         if frecuencia_paradas is not False:
#             n_paradas = int(
#                 distancia / (velocidad_cam * 60 * frecuencia_paradas)
#             )  # minutos de parada, cada cuanto parar
#             if n_paradas > 0:
#                 print(f"Paradas: {n_paradas}")
#                 distancias_paradas = np.linspace(0, distancia, n_paradas + 1)
#                 for dist in distancias_paradas[1:]:  # Saltamos el 0 inicial
#                     print(f"Distancia: {dist:.2f} metros")
#                     # Calculate the coordinates of the point at the given distance
#                     mid_coords = (
#                         start_coords[0]
#                         + (end_coords[0] - start_coords[0]) * (dist / distancia),
#                         start_coords[1]
#                         + (end_coords[1] - start_coords[1]) * (dist / distancia),
#                     )
#                     nearest_fountain = ox.distance.nearest_nodes(
#                         graph, mid_coords[1], mid_coords[0]
#                     )
#                     # Calculate the distance to the nearest fountain
#                     node_data = graph.nodes[nearest_fountain]

#                     start = (node_data["y"], node_data["x"])
#                     end = (float(mid_coords[0]), float(mid_coords[1]))
#                     distance = get_distance(start, end)
#                     print(f"Distancia a la fuente: {distance:.2f} metros")
#                     if distance <= max_distance:
#                         fountains.append(nearest_fountain)
#                         print(
#                             f"Fuente encontrada: {nearest_fountain} a {distance:.2f} metros de la ruta"
#                         )

#     elif type_displacement == "En Bicicleta" or type_displacement == "En ValenBisi":
#         if type_displacement == "En ValenBisi":
#             type_displacement = "En Bicicleta"

#         max_distance = 200
#         velocidad_bic = 2.6  # m/s, velocidad media en bicicleta con semaforos, normalmente se va a ~4 m/s
#         frecuencia_paradas = obtener_frecuencia_paradas()

#         if frecuencia_paradas is not False:
#             n_paradas = int(
#                 distancia / (velocidad_bic * 60 * frecuencia_paradas)
#             )  # minutos de parada, cada cuanto parar
#             if n_paradas > 0:
#                 print(f"Paradas: {n_paradas}")
#                 distancias_paradas = np.linspace(0, distancia, n_paradas + 1)
#                 for dist in distancias_paradas[1:]:  # Saltamos el 0 inicial
#                     print(f"Distancia: {dist:.2f} metros")
#                     # Calculate the coordinates of the point at the given distance
#                     mid_coords = (
#                         start_coords[0]
#                         + (end_coords[0] - start_coords[0]) * (dist / distancia),
#                         start_coords[1]
#                         + (end_coords[1] - start_coords[1]) * (dist / distancia),
#                     )
#                     nearest_fountain = ox.distance.nearest_nodes(
#                         graph, mid_coords[1], mid_coords[0]
#                     )
#                     # Calculate the distance to the nearest fountain
#                     node_data = graph.nodes[nearest_fountain]

#                     start = (node_data["y"], node_data["x"])
#                     end = (float(mid_coords[0]), float(mid_coords[1]))
#                     distance = get_distance(start, end)
#                     print(f"Distancia a la fuente: {distance:.2f} metros")
#                     if distance <= max_distance:
#                         fountains.append(nearest_fountain)
#                         print(
#                             f"Fuente encontrada: {nearest_fountain} a {distance:.2f} metros de la ruta"
#                         )

#     return fountains

### Cogiendo las posiciones de las fuentes del gpd

In [152]:
import osmnx as ox
import numpy as np
from scipy.spatial import cKDTree
from math import radians, sin, cos, sqrt, atan2


def get_nearest_water_fountains_on_route(
    graph, distancia, route_nodes, type_displacement, temperatura, fuentes_publicas_gpd
):
    """
    Find the nearest public water fountains along a given route, using pre-loaded fountain GeoDataFrame.

    Parameters:
        graph: The cycling network graph.
        distancia (float): Total length of the route in meters.
        route_nodes (list): A list of nodes representing the route.
        type_displacement (str): "Caminando", "En Bicicleta" or "En ValenBisi".
        temperatura (float): Current temperature in °C.
        fuentes_publicas_gpd (GeoDataFrame): GeoDataFrame of public fountains with geometry column.

    Returns:
        list: A list of node IDs for fountains within max_distance of each stop point.
    """
    # Preprocess fountain coordinates and build KD-tree
    fountain_nodes = fuentes_publicas_gpd.index.to_list()
    fountain_coords = np.array([(pt.y, pt.x) for pt in fuentes_publicas_gpd.geometry])
    tree = cKDTree(fountain_coords)

    # Helper: haversine distance in meters
    def haversine(a, b):
        R = 6_371_000  # Earth radius in meters
        lat1, lon1 = map(radians, a)
        lat2, lon2 = map(radians, b)
        dlat, dlon = lat2 - lat1, lon2 - lon1
        u = sin(dlat / 2) ** 2 + cos(lat1) * cos(lat2) * sin(dlon / 2) ** 2
        return 2 * R * atan2(sqrt(u), sqrt(1 - u))

    # Temperature-based stop frequency
    freq_config = {
        "frio": {"min": -50, "max": 10, "Caminando": 7, "En Bicicleta": 12},
        "ideal": {"min": 15, "max": 25, "Caminando": 5, "En Bicicleta": 9},
        "calor_extremo": {"min": 30, "max": 50, "Caminando": 3, "En Bicicleta": 6},
    }

    def obtener_frecuencia():
        if temperatura < 10:
            return freq_config["frio"][type_displacement]
        elif 15 <= temperatura <= 25:
            return freq_config["ideal"][type_displacement]
        elif temperatura > 30:
            return freq_config["calor_extremo"][type_displacement]
        else:
            return None

    # Determine speed and max_distance
    if type_displacement == "Caminando":
        velocidad = 1.0  # m/s
        max_distance = 150  # meters
    else:
        velocidad = 2.6  # m/s (both bicycle and ValenBisi)
        max_distance = 200  # meters

    frecuencia = obtener_frecuencia()
    if frecuencia is None:
        return []

    n_paradas = int(distancia / (velocidad * 60 * frecuencia))
    if n_paradas <= 0:
        return []

    # Generate intermediate stop distances
    d = distancia / n_paradas
    resultados = []
    # # Coordinates of route start and end
    # start = (graph.nodes[route_nodes[0]]["y"], graph.nodes[route_nodes[0]]["x"])
    # end = (graph.nodes[route_nodes[-1]]["y"], graph.nodes[route_nodes[-1]]["x"])

    # for d in distancias:
    #     # linear interpolation along start->end
    #     frac = d / distancia
    #     mid = (
    #         start[0] + (end[0] - start[0]) * frac,
    #         start[1] + (end[1] - start[1]) * frac,
    #     )
    #     # Query KD-tree (returns in degrees)
    #     _, idx = tree.query([mid], k=1)
    #     fountain_idx = fountain_nodes[idx[0]]
    #     fountain_pt = fuentes_publicas_gpd.loc[fountain_idx].geometry
    #     # Compute true meter distance
    #     d_m = haversine(mid, (fountain_pt.y, fountain_pt.x))
    #     print(f"Distancia a la fuente {fountain_idx}: {d_m:.2f} metros")
    #     print(f"Fuente encontrada: {max_distance}")
    #     if d_m <= max_distance:
    #         resultados.append(fountain_idx)

    d_accum = 0.0
    parada = 1

    for i in range(len(route_nodes) - 1):
        edge_info = graph.get_edge_data(route_nodes[i], route_nodes[i + 1])

        d_accum += edge_info[0]["length"]
        if d_accum >= parada * d:
            _, idx = tree.query(
                [(graph.nodes[route_nodes[i]]["y"], graph.nodes[route_nodes[i]]["x"])],
                k=1,
            )
            fountain_idx = fountain_nodes[idx[0]]
            fountain_pt = fuentes_publicas_gpd.loc[fountain_idx].geometry
            d_m = haversine(
                (graph.nodes[route_nodes[i]]["y"], graph.nodes[route_nodes[i]]["x"]),
                (fountain_pt.y, fountain_pt.x),
            )
            parada += 1
            if d_m <= max_distance:
                resultados.append(fountain_idx)

    return resultados


### Está mal

In [153]:
# import osmnx as ox
# import numpy as np
# from geopy.distance import geodesic


# def get_distance(coord1, coord2):
#     return geodesic(coord1, coord2).meters


# def get_nearest_water_fountains_on_route(
#     graph, distancia, route_nodes, type_displacement, temperatura
# ):
#     fountains_found = set()
#     fountain_results = []

#     # Definir velocidades y frecuencias según temperatura
#     frecs = {
#         "frio": {"min": -50, "max": 10, "Caminando": 7, "En Bicicleta": 12},
#         "ideal": {"min": 15, "max": 25, "Caminando": 5, "En Bicicleta": 9},
#         "calor_extremo": {"min": 30, "max": 50, "Caminando": 3, "En Bicicleta": 6},
#     }

#     def get_frecuencia():
#         for clima, rango in frecs.items():
#             if rango["min"] <= temperatura <= rango["max"]:
#                 return rango[type_displacement]
#         return None

#     # Velocidades en m/s
#     velocidad = 1 if type_displacement == "Caminando" else 2.6
#     max_dist = 150 if type_displacement == "Caminando" else 200
#     if type_displacement == "En ValenBisi":
#         type_displacement = "En Bicicleta"

#     frecuencia_paradas = get_frecuencia()
#     if frecuencia_paradas is None:
#         return []

#     # Calcular puntos a lo largo de toda la ruta
#     n_paradas = int(distancia / (velocidad * 60 * frecuencia_paradas))
#     if n_paradas == 0:
#         return []

#     # Convertir ruta a coordenadas
#     route_coords = [(graph.nodes[n]["y"], graph.nodes[n]["x"]) for n in route_nodes]
#     cumulative_distance = [0]

#     # Calcular distancias acumuladas para interpolar
#     for i in range(1, len(route_coords)):
#         seg_dist = get_distance(route_coords[i - 1], route_coords[i])
#         cumulative_distance.append(cumulative_distance[-1] + seg_dist)

#     # Distancias a las que buscar fuentes
#     sample_dists = np.linspace(0, cumulative_distance[-1], n_paradas + 1)[1:]

#     for target_dist in sample_dists:
#         for i in range(1, len(cumulative_distance)):
#             if cumulative_distance[i] >= target_dist:
#                 ratio = (target_dist - cumulative_distance[i - 1]) / (
#                     cumulative_distance[i] - cumulative_distance[i - 1]
#                 )
#                 lat1, lon1 = route_coords[i - 1]
#                 lat2, lon2 = route_coords[i]
#                 mid_lat = lat1 + ratio * (lat2 - lat1)
#                 mid_lon = lon1 + ratio * (lon2 - lon1)

#                 nearest_node = ox.distance.nearest_nodes(graph, mid_lon, mid_lat)
#                 coord_node = (
#                     graph.nodes[nearest_node]["y"],
#                     graph.nodes[nearest_node]["x"],
#                 )
#                 dist_to_mid = get_distance((mid_lat, mid_lon), coord_node)

#                 if dist_to_mid <= max_dist and nearest_node not in fountains_found:
#                     fountains_found.add(nearest_node)
#                     fountain_results.append(nearest_node)
#                 break  # saltamos al siguiente target_dist tras primer match

#     return fountain_results


Calculo distancia en metros

In [154]:
import math


def get_distance(start, end):
    """
    Calculate the distance between two geographic points.

    Parameters:
        start (tuple): (lat, lon) in decimal degrees.
        end   (tuple): (lat, lon) in decimal degrees.

    Returns:
        deg_dist (float): Euclidean distance in decimal degrees.
        gc_dist_m (float): Great-circle distance in meters.
    """
    lat1, lon1 = map(math.radians, start)
    lat2, lon2 = map(math.radians, end)

    # 2. Haversine (great-circle) in meters
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = (
        math.sin(dlat / 2) ** 2
        + math.cos(lat1) * math.cos(lat2) * math.sin(dlon / 2) ** 2
    )
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    R = 6371000  # Earth radius in meters
    gc_dist_m = R * c

    return gc_dist_m

### Extracción ruta a partir de dos puntos

In [155]:
def get_route(start, end, graph):
    """
    Get the route between two nodes in the graph.

    Parameters:
        start(tuple): Tuple of coordenates for the start point.
        end: Tuple of coordinates for the end point.
        graph: The cycling network graph.

    Returns:
        list: A list of nodes representing the route.
    """
    from_node = ox.distance.nearest_nodes(graph, start[1], start[0])
    to_node = ox.distance.nearest_nodes(graph, end[1], end[0])
    distancia = get_distance(
        start, end
    )  # [1]  # Get the great-circle distance in meters
    route = ox.shortest_path(graph, from_node, to_node, weight="length")
    return route, distancia


# Example usage
start = (39.4699, -0.3763)  # Example start coordinates (Valencia center)
end = (39.48098, -0.3484897)  # Example end coordinates (somewhere else in Valencia)
route, distancia = get_route(start, end, cycle_graph)

### Prueba fuentes

In [156]:
fountains_on_route = get_nearest_water_fountains_on_route(
    cycle_graph,  # 1️⃣ tu grafo OSMnx, no el mapa
    distancia,  # 2️⃣ longitud total de la ruta en metros
    route,  # 3️⃣ lista de nodos que componen la ruta
    "Caminando",  # 4️⃣ tipo de desplazamiento
    20,  # 5️⃣ temperatura en °C
    fuentes_publicas_gpd,  # 6️⃣ tu GeoDataFrame de fuentes públicas
)


### VISIONADO PUNTOS FUENTES

In [157]:
for i in fountains_on_route:
    print(
        fuentes_publicas_gpd.loc[i, "geometry"]
    )  # Get the centroid coordinates of each fountain

POINT (-0.3688589936206121 39.47247695903695)
POINT (-0.3626880047060055 39.47240447920339)
POINT (-0.3596560064928804 39.47336196807246)
POINT (-0.3541109863120086 39.477333067703064)


# Observación de las rutas en mapa

In [158]:
import osmnx as ox
import folium
from shapely.geometry import shape
import sys

sys.path.append("../src/")
from utils import (
    get_route,
    get_nearest_station,
    get_valencian_open_data,
    get_valenbisi_stations,
)

cycling_graph = ox.load_graphml("../data/valencia_cycling_network.graphml")
walking_graph = ox.load_graphml("../data/valencia_walking_network.graphml")


def get_valenbisi_route(start, end, cycling_graph, walking_graph, valenbisi_stations):
    """
    Get the Valenbisi route from start to end using the cycling network graph.

    Parameters:
        start(tuple): Tuple of coordinates for the start point.
        end(tuple): Tuple of coordinates for the end point.
        cycling_graph: The cycling network graph.
        walking_graph: The walking network graph.
        valenbisi_stations(geoDataFrame): A GeoDataFrame containing Valenbisi stations.

    Returns:
        tuple: A tuple containing three lists:
            - The walking route from the start to the nearest Valenbisi station.
            - The cycling route between the two Valenbisi stations.
            - The walking route from the nearest Valenbisi station to the end point.
            - The nearest Valenbisi station to the start point.
            - The nearest Valenbisi station to the end point.
    """

    threshold = 0.0001

    cycling_nearest_node = ox.distance.nearest_nodes(
        cycling_graph, X=start[1], Y=start[0]
    )

    ini_valenbisi_station = valenbisi_stations[
        valenbisi_stations["available"] > 0
    ].copy()
    end_valenbisi_station = valenbisi_stations[valenbisi_stations["free"] > 0].copy()

    ini_station = get_nearest_station(
        (
            cycling_graph.nodes[cycling_nearest_node]["y"],
            cycling_graph.nodes[cycling_nearest_node]["x"],
        ),
        ini_valenbisi_station,
    )
    end_station = get_nearest_station(end, end_valenbisi_station)

    ini_station_loc = ini_station["geo_point_2d"]
    end_station_loc = end_station["geo_point_2d"]

    ini_walking_route = get_route(
        start, (ini_station_loc["lat"], ini_station_loc["lon"]), walking_graph
    )
    end_walking_route = get_route(
        (end_station_loc["lat"], end_station_loc["lon"]), end, walking_graph
    )
    cycling_route = get_route(
        (ini_station_loc["lat"], ini_station_loc["lon"]),
        (end_station_loc["lat"], end_station_loc["lon"]),
        cycling_graph,
    )

    dist_ini_station = ox.distance.euclidean(
        ini_station_loc["lat"],
        ini_station_loc["lon"],
        cycling_graph.nodes[cycling_route[0]]["y"],
        cycling_graph.nodes[cycling_route[0]]["x"],
    )

    dist_end_station = ox.distance.euclidean(
        end_station_loc["lat"],
        end_station_loc["lon"],
        cycling_graph.nodes[cycling_route[-1]]["y"],
        cycling_graph.nodes[cycling_route[-1]]["x"],
    )

    if dist_ini_station > threshold:
        inter_ini = get_route(
            (ini_station_loc["lat"], ini_station_loc["lon"]),
            (
                cycling_graph.nodes[cycling_route[0]]["y"],
                cycling_graph.nodes[cycling_route[0]]["x"],
            ),
            walking_graph,
        )
        ini_walking_route.extend(inter_ini)
    if dist_end_station > threshold:
        inter_end = get_route(
            (
                cycling_graph.nodes[cycling_route[-1]]["y"],
                cycling_graph.nodes[cycling_route[-1]]["x"],
            ),
            (end_station_loc["lat"], end_station_loc["lon"]),
            walking_graph,
        )
        end_walking_route = inter_end + end_walking_route

    return ini_walking_route, cycling_route, end_walking_route, ini_station, end_station

In [159]:
params = {
    "rows": 100,
}
url = "https://valencia.opendatasoft.com//api/explore/v2.1/catalog/datasets/valenbisi-disponibilitat-valenbisi-dsiponibilidad/records"
valenbisi_stations = get_valencian_open_data(url, params)

valenbisi_stations["geometry"] = valenbisi_stations["geo_shape"].apply(shape)
valenbisi_stations = get_valenbisi_stations(valenbisi_stations)
valenbisi_stations = valenbisi_stations[valenbisi_stations["open"] == "T"]

start = (39.4699, -0.3763)  # Example start coordinates (Valencia city center)
end = (39.48098, -0.3484897)  # Example end coordinates (nearby location)


ini_walking_route, cycling_route, end_walking_route, ini_station, end_station = (
    get_valenbisi_route(start, end, cycling_graph, walking_graph, valenbisi_stations)
)

m = folium.Map(location=start, zoom_start=14)

folium.PolyLine(
    locations=[
        (walking_graph.nodes[node]["y"], walking_graph.nodes[node]["x"])
        for node in ini_walking_route
    ],
    color="green",
    weight=5,
    opacity=0.7,
).add_to(m)

folium.PolyLine(
    locations=[
        (cycling_graph.nodes[node]["y"], cycling_graph.nodes[node]["x"])
        for node in cycling_route
    ],
    color="blue",
    weight=5,
    opacity=0.7,
).add_to(m)

folium.PolyLine(
    locations=[
        (walking_graph.nodes[node]["y"], walking_graph.nodes[node]["x"])
        for node in end_walking_route
    ],
    color="green",
    weight=5,
    opacity=0.7,
).add_to(m)


ini_station_loc = ini_station["geo_point_2d"]
end_station_loc = end_station["geo_point_2d"]

# Salida y llegada
folium.Marker(
    location=(start[0], start[1]),
    popup="Start",
    icon=folium.Icon(color="blue"),
).add_to(m)

folium.Marker(
    location=(end[0], end[1]),
    popup="End",
    icon=folium.Icon(color="blue"),
).add_to(m)


# Cambiar el marquer de forma que muestre una bici y un número de bicis en el propio marcador
folium.Marker(
    location=(ini_station_loc["lat"], ini_station_loc["lon"]),
    popup=f"Start Station.<br>Available Bikes: {ini_station['available']}",
    icon=folium.Icon(color="green", icon="bicycle", prefix="fa"),
).add_to(m)


folium.Marker(
    location=(end_station_loc["lat"], end_station_loc["lon"]),
    popup=f"End Station: {end_station['address']}<br>Available Places: {end_station['free']}",
    icon=folium.Icon(color="red", icon="home"),
).add_to(m)


Total records found: 273


In [160]:
for idx in fountains_on_route:
    calle = fuentes_publicas_gpd.loc[idx, "calle"]
    pt = fuentes_publicas_gpd.loc[idx].geometry
    folium.Marker(
        location=(pt.y, pt.x),  # latitud, longitud
        popup=f"Fuente calle {calle}",
        icon=folium.Icon(color="blue", icon="tint", prefix="fa"),
    ).add_to(m)


In [161]:
m